## map2graph

### load base project

                  """
                  
                  geology_file="./source_data/geol_clip.shp",
                  #fault_file="./empty_faults2.shp",
                  fault_file="./source_data/faults_clip.shp",
                  fold_file="./source_data/folds_clip.shp",
                  structure_file="./source_data/structure_clip.shp",
                  mindep_file="./source_data/mindeps_clip.shp",
                  #mindep_file="./empty_mindeps2.shp",
                  #loopdata_state = "WA",
                  dtm_file='./source_data/dtm_rp.tif',
                  metadata='./source_data/pre_graph.hjson'
                  
                  geology_file="./Example2_Yilgarn/tmp/geol_clip.shp",
                  #fault_file="./empty_faults2.shp",
                  fault_file="./Example2_Yilgarn/tmp/faults_clip.shp",
                  fold_file="./Example2_Yilgarn/tmp/folds_clip.shp",
                  structure_file="./Example2_Yilgarn/tmp/structure_clip.shp",
                  mindep_file="./Example2_Yilgarn/tmp/mindeps_clip.shp",
                  #mindep_file="./empty_mindeps2.shp",
                  #loopdata_state = "WA",
                  dtm_file='./Example2_Yilgarn/dtm/dtm_rp.tif',
                  metadata='./source_data/pre_graph.hjson'
                  
                  """

In [1]:
import os
import shutil
from map2loop.project import Project
from map2loop.topology import Topology
import pandas as pd
import geopandas as gpd
import numpy as np
import networkx as nx
from geopandas import GeoDataFrame
from pandas import DataFrame
from shapely.geometry import Polygon, LineString, Point, MultiLineString, MultiPolygon
from shapely.ops import snap
import time
from map2loop import m2l_utils, map2graph
from math import acos, degrees
time0=time.time()
proj = Project( 
                  
                  geology_file="./source_data/geol_clip.shp",
                  #fault_file="./empty_faults2.shp",
                  fault_file="./source_data/faults_clip.shp",
                  fold_file="./source_data/folds_clip.shp",
                  structure_file="./source_data/structure_clip.shp",
                  mindep_file="./source_data/mindeps_clip.shp",
                  #mindep_file="./empty_mindeps2.shp",
                  #loopdata_state = "WA",
                  dtm_file='./source_data/dtm_rp.tif',
                  metadata='./source_data/pre_graph.hjson'
                  
                )



commodity="NONE"
commodity="Fe,Cu,Au,NONE"
close_f=2000
close_b=2000
close_i=2000
fault_clip_buffer=0.01
snap_buffer=.5

fault_fault_weight=3
fault_weight=1
formation_weight=7
formation_formation_weight=9
fault_formation_weight=5

output_path='./map2loopResources'
if (os.path.exists(output_path)):
    shutil.rmtree(output_path)
graph_path=os.path.join(output_path, 'graph')
gis_path=os.path.join(output_path, 'gis')
os.mkdir(output_path)
os.mkdir(graph_path)
os.mkdir(gis_path)

In [2]:
mindep=gpd.read_file(proj.mindep_file)
fault=gpd.read_file(proj.fault_file)
geology=gpd.read_file(proj.geology_file)

fault_clean = fault.dropna(subset=['geometry'])
geology_clean_nona = geology.dropna(subset=['geometry'])

fault_zone = fault_clean.buffer(fault_clip_buffer)
all_fz = fault_zone.unary_union

geology_clean=geology_clean_nona.difference(all_fz)
geology_clean=gpd.GeoDataFrame(geology, crs=geology.crs, geometry=geology_clean.geometry)


In [3]:
geology_exploded=geology_clean.explode()
geology_exploded.reset_index(inplace=True)
geology_exploded['idx']=geology_exploded.index
#geology_exploded.to_file(os.path.join(gis_path, 'exploded_geology.shp'))


### Calculate stratigraphy graph

In [4]:
all_contacts=[]
for ind,g in geology_exploded.iterrows():
    for ind2,g2 in geology_exploded.iterrows():
        if(not ind >= ind2):
            if(g.geometry.intersects(g2.geometry)):
                g1_snapped = snap(g.geometry, g2.geometry,snap_buffer)
                all_contacts.append([ind,ind2,g1_snapped.buffer(0).intersection(g2.geometry.buffer(0))])
                

In [5]:
groups=geology_exploded.drop_duplicates(subset=[proj.c_l['g']])
groups.reset_index(inplace=True)
groups['order'] = groups.index
groups.set_index([proj.c_l['g']],inplace=True)
    
strats=geology_exploded.drop_duplicates(subset=[proj.c_l['c']])
strats[proj.c_l['c']]=strats[proj.c_l['c']].str.replace(' ','_').replace('-','_')
strats.set_index([proj.c_l['c']],inplace=True)

Gloop=nx.DiGraph()

index=0

for ind,p in geology_exploded.iterrows():
    Gloop.add_node(ind,id=index, formation=p[proj.c_l['c']].replace(" ","_").replace("-","_"),LabelGraphics ='[ text "'+geology_exploded.iloc[ind][proj.c_l['c']].replace(' ','_').replace('-','_')+'_'+str(ind)+'" anchor "n" fontStyle "bold" fontSize 14 ]')
    Gloop.nodes[ind]['ntype']='formation'
    Gloop.nodes[ind]['weight']=formation_weight
    index=index+1


for c in all_contacts:
    ave_age0=int(geology_exploded.iloc[c[0]][proj.c_l['min']])+((int(geology_exploded.iloc[c[0]][proj.c_l['max']])-int(geology_exploded.iloc[c[0]][proj.c_l['min']]))/2)
    ave_age1=int(geology_exploded.iloc[c[1]][proj.c_l['min']])+((int(geology_exploded.iloc[c[1]][proj.c_l['max']])-int(geology_exploded.iloc[c[1]][proj.c_l['min']]))/2)

    if(ave_age0>ave_age1):
        Gloop.add_edge(geology_exploded.iloc[c[1]].name,geology_exploded.iloc[c[0]].name)
        Gloop[geology_exploded.iloc[c[1]].name][geology_exploded.iloc[c[0]].name]['etype']='formation_formation'
        Gloop[geology_exploded.iloc[c[1]].name][geology_exploded.iloc[c[0]].name]['formation1']=geology_exploded.iloc[c[0]][proj.c_l['c']].replace(' ','_').replace('-','_')+'_'+str(geology_exploded.iloc[c[0]]['idx'])
        Gloop[geology_exploded.iloc[c[1]].name][geology_exploded.iloc[c[0]].name]['formation2']=geology_exploded.iloc[c[1]][proj.c_l['c']].replace(' ','_').replace('-','_')+'_'+str(geology_exploded.iloc[c[1]]['idx'])
        Gloop[geology_exploded.iloc[c[1]].name][geology_exploded.iloc[c[0]].name]['weight']=formation_formation_weight
    else:
        Gloop.add_edge(geology_exploded.iloc[c[0]].name,geology_exploded.iloc[c[1]].name)
        Gloop[geology_exploded.iloc[c[0]].name][geology_exploded.iloc[c[1]].name]['etype']='formation_formation'
        Gloop[geology_exploded.iloc[c[0]].name][geology_exploded.iloc[c[1]].name]['formation1']=geology_exploded.iloc[c[1]][proj.c_l['c']].replace(' ','_').replace('-','_')+'_'+str(geology_exploded.iloc[c[1]]['idx'])
        Gloop[geology_exploded.iloc[c[0]].name][geology_exploded.iloc[c[1]].name]['formation2']=geology_exploded.iloc[c[0]][proj.c_l['c']].replace(' ','_').replace('-','_')+'_'+str(geology_exploded.iloc[c[0]]['idx'])
        Gloop[geology_exploded.iloc[c[0]].name][geology_exploded.iloc[c[1]].name]['weight']=formation_formation_weight
        
nx.write_gml(Gloop, os.path.join(graph_path, 'granular_pre_loop.gml'))


In [6]:
def fix_Loop_graph(output_path,prefix):
        with open(os.path.join(output_path,prefix+'.gml')) as graph:
            new_graph=open(os.path.join(output_path,prefix+'_fixed.gml'),"w")
            lines = graph.readlines()
            for l in lines:
                l=l.replace('&#34;','"').replace('"[','[').replace(']"',']')
                if('gid "' in l):
                    tmp=l.split('"')
                    new_graph.write('    gid '+str(int(tmp[1])-1)+'\n')                
                else:
                    new_graph.write(l)
            new_graph.close()
            
fix_Loop_graph(graph_path,'granular_pre_loop')


#Topology.use_asud('granular_pre_loop_fixed.gml', './')

### Calculate fault intersections

In [7]:
Gloop=nx.read_gml(os.path.join(graph_path, 'granular_pre_loop_fixed.gml'))
Gfault=nx.DiGraph()
fault_intersections=[]

for ind,f in fault_clean.iterrows():
    Gloop.add_node('Fault_'+f[proj.c_l['o']])
    Gloop.nodes['Fault_'+f[proj.c_l['o']]]['ntype']='fault'
    Gloop.nodes['Fault_'+f[proj.c_l['o']]]['weight']=fault_weight
    Gfault.add_node('Fault_'+f[proj.c_l['o']])
    Gfault.nodes['Fault_'+f[proj.c_l['o']]]['ntype']='fault'
    for ind2,f2 in fault_clean.iterrows():
        if(not fault_clean.iloc[ind][proj.c_l['o']]>=fault_clean.iloc[ind2][proj.c_l['o']]):
            if(f.geometry.intersects(f2.geometry)):
                fault_intersections.append([fault_clean.iloc[ind][proj.c_l['o']],fault_clean.iloc[ind2][proj.c_l['o']],f.geometry.intersection(f2.geometry)])

fault_name=fault_clean.set_index(proj.c_l['o'])
eps=.01
min_ang=30
for ind,f in fault_name.iterrows():
    for e in fault_intersections:
        if(e[0]==f.name):
            other=e[1]
        else:
            other=e[0]
        if(e[2].distance(Point(f.geometry.coords[0]))<eps):
            ind2=0
            for pt in fault_name.loc[other].geometry.coords[1:-1]:
                if(Point(pt).distance(e[2])<eps):
                    l1,m1=m2l_utils.pts2dircos(f.geometry.coords[0][0],f.geometry.coords[0][1],f.geometry.coords[1][0],f.geometry.coords[1][1])
                    l2,m2=m2l_utils.pts2dircos(fault_name.loc[other].geometry.coords[ind2-1][0],fault_name.loc[other].geometry.coords[ind2-1][1],
                                   fault_name.loc[other].geometry.coords[ind2+1][0],fault_name.loc[other].geometry.coords[ind2+1][1])
                    ang=degrees(acos(l1*l2+m1*m2))
                    if(ang>90):
                        ang=180-ang
                    if(ang<min_ang):
                        ang_code='T'
                    else:
                        ang_code='X'

                    Gloop.add_edge('Fault_'+f.name,'Fault_'+other)
                    Gloop['Fault_'+f.name]['Fault_'+other]['etype']='fault_fault'
                    Gloop['Fault_'+f.name]['Fault_'+other]['fault1']='Fault_'+f.name
                    Gloop['Fault_'+f.name]['Fault_'+other]['fault2']='Fault_'+other
                    Gloop['Fault_'+f.name]['Fault_'+other]['angle']=int(ang)
                    Gloop['Fault_'+f.name]['Fault_'+other]['topol']=ang_code
                    Gloop['Fault_'+f.name]['Fault_'+other]['weight']=fault_fault_weight
                    
                    """Gfault.add_edge('Fault_'+f.name,'Fault_'+other)
                    Gfault['Fault_'+f.name]['Fault_'+other]['etype']='fault_fault'
                    Gfault['Fault_'+f.name]['Fault_'+other]['angle']=int(ang)
                    Gfault['Fault_'+f.name]['Fault_'+other]['topol']=ang_code
                    Gfault['Fault_'+f.name]['Fault_'+other]['weight']=fault_fault_weight"""
                ind2=ind2+1
        
        elif(e[2].distance(Point(f.geometry.coords[-1]))<eps):
            ind2=0
            for pt in fault_name.loc[other].geometry.coords[1:-1]:
                if(Point(pt).distance(e[2])<eps):
                    l1,m1=m2l_utils.pts2dircos(f.geometry.coords[-1][0],f.geometry.coords[-1][1],f.geometry.coords[-2][0],f.geometry.coords[-2][1])
                    l2,m2=m2l_utils.pts2dircos(fault_name.loc[other].geometry.coords[ind2-1][0],fault_name.loc[other].geometry.coords[ind2-1][1],
                                   fault_name.loc[other].geometry.coords[ind2+1][0],fault_name.loc[other].geometry.coords[ind2+1][1])
                    ang=degrees(acos(l1*l2+m1*m2))
                    if(ang>90):
                        ang=180-ang
                    if(ang<min_ang):
                        ang_code='T'
                    else:
                        ang_code='X'
                    Gloop.add_edge('Fault_'+f.name,'Fault_'+other)
                    Gloop['Fault_'+f.name]['Fault_'+other]['etype']='fault_fault'
                    Gloop['Fault_'+f.name]['Fault_'+other]['fault1']='Fault_'+f.name
                    Gloop['Fault_'+f.name]['Fault_'+other]['fault2']='Fault_'+other
                    Gloop['Fault_'+f.name]['Fault_'+other]['angle']=int(ang)
                    Gloop['Fault_'+f.name]['Fault_'+other]['topol']=ang_code
                    Gloop['Fault_'+f.name]['Fault_'+other]['weight']=fault_fault_weight
                    
                    """Gfault.add_edge('Fault_'+f.name,'Fault_'+other)
                    Gfault['Fault_'+f.name]['Fault_'+other]['etype']='fault_fault'
                    Gfault['Fault_'+f.name]['Fault_'+other]['angle']=int(ang)
                    Gfault['Fault_'+f.name]['Fault_'+other]['topol']=ang_code
                    Gfault['Fault_'+f.name]['Fault_'+other]['weight']=fault_fault_weight"""

                ind2=ind2+1

nx.write_gml(Gfault, os.path.join(graph_path, 'granular_fault_network.gml'))


### calculate fault-formation intersections

In [8]:
fault_group_array=np.zeros((len(groups),len(fault_clean)), dtype=np.int8)
fault_names='Fault_'+fault_clean[proj.c_l['o']]
group_names=list(groups.index)
group_names=[w.replace(" ","_").replace("-","_") for w in group_names]

i1=0
for ind,f in fault_clean.iterrows():
    for ind2,g in geology_exploded.iterrows():
        if(f.geometry.intersects(g.geometry.buffer(snap_buffer).buffer(0))):
            #print('Fault_'+f[proj.c_l['o']])
            g1_snapped = snap(g.geometry.buffer(snap_buffer).buffer(0), f.geometry.buffer(0),snap_buffer)
            x=g1_snapped.intersection(f.geometry)
            if(x.geom_type!='Point' and x.geom_type!='MultiPoint' ):
                Gloop.add_edge('Fault_'+f[proj.c_l['o']],str(g.name))
                Gloop['Fault_'+f[proj.c_l['o']]][str(g.name)]['etype']='fault_formation'
                Gloop['Fault_'+f[proj.c_l['o']]][str(g.name)]['weight']=fault_formation_weight
                Gloop['Fault_'+f[proj.c_l['o']]][str(g.name)]['fault']='Fault_'+f[proj.c_l['o']]
                Gloop['Fault_'+f[proj.c_l['o']]][str(g.name)]['formation']=str(g[proj.c_l['c']].replace(" ","_").replace("-","_"))+'_'+str(g['idx'])
                #print("'"+str(g.name)+"'",str(ind2))
                
                #fault_group_array[groups.loc[g[proj.c_l['g'].replace(" ","_").replace("-","_")]]['order'],i1]=1
    i1=i1+1
#fault_group_df=pd.DataFrame(fault_group_array,index=group_names,columns=fault_names)
#fault_group_df.to_csv('group-fault-relationships.csv',index_label='group')      


### Add mineralisation info to graphs and shapefiles

In [12]:
commodities=commodity.split(',')
if(not 'NONE' in commodity):
    commodities.append('NONE')
fault_tmp=fault.copy()
geology_exploded_tmp=geology_exploded.copy()
#i_contacts_gdf_tmp=i_contacts_gdf.copy()
mindep_geology = gpd.sjoin(mindep, geology_exploded, how="left", op="within")

for com in commodities:
    if(not com == 'NONE'):
        mindep_com=mindep_geology[mindep_geology[proj.c_l['mcom']]==com]

        if(len(mindep_com)>0):
          
            for ind,m in mindep_com.iterrows():
                fault_tmp['d_'+str(ind)]=fault_tmp.distance(Point(m.geometry))

            gc=[]
            for ind,g in geology_exploded_tmp.iterrows():
                fm_count=0
                for ind2,m in mindep_com.iterrows():
                    if(m[proj.c_l['c']]==g[proj.c_l['c']]):
                        fm_count=fm_count+1
                        #print('fm_count',fm_count)    
                gc.append(fm_count)
            geology_exploded_tmp[com+'_min']=gc    
            
            gc=[]
            for ind,g in geology_exploded.iterrows():
                fm_count=0
                for ind2,m in mindep_com.iterrows():
                    if(m[proj.c_l['c']]==g[proj.c_l['c']]):
                        fm_count=fm_count+1
                        #print('fm_count',fm_count)    
                gc.append(fm_count)
            geology_exploded[com+'_min']=gc    

            fc=[]
            for ind,f in fault_tmp.iterrows():
                fault_count=0
                for ind2,m in mindep_com.iterrows():
                    if(f['d_'+str(ind2)]<close_f):
                        fault_count=fault_count+1
                fc.append(fault_count)
            fault[com+'_min']=fc    

            for ind,b in geology_exploded.iterrows():
                Gloop.nodes[str(ind)][com+'_min']=b[com+'_min']

            for ind,f in fault.iterrows():
                Gloop.nodes['Fault_'+f[proj.c_l['o']]][com+'_min']=f[com+'_min']

        else:
            for ind,b in geology_exploded_tmp.iterrows():
                Gloop.nodes[str(b.name)][com+'_min']=-1

            for ind,f in fault.iterrows():
                Gloop.nodes['Fault_'+f[proj.c_l['o']]][com+'_min']=-1

        
        
if(len(geology_exploded_tmp)>0):
    geology_exploded_tmp.to_file(os.path.join(gis_path, 'exploded_geology_min.shp'))
if(len(geology_exploded)>0):
    geology_exploded_tmp.to_file(os.path.join(gis_path, 'unexploded_geology_min.shp'))
if(len(mindep_geology)>0):
    mindep_geology.to_file(os.path.join(gis_path, 'mindep_geology.shp'))    
if(len(fault)>0):
    fault.to_file(os.path.join(gis_path, 'mindep_fault.shp')) 
    
nx.write_gml(Gloop, os.path.join(graph_path, 'granular_pre_loop_mindep.gml'))
Topology.colour_Loop_graph( graph_path,'granular_pre_loop_mindep')
map2graph.Map2Graph.fix_Loop_graph(graph_path,'granular_pre_loop_mindep_colour')

In [10]:
source='102'
#source='286'
new_weight=1000
Gloopu=Gloop.to_undirected()
Gloopu.nodes['Fault_3498']['weight']=new_weight
Gloopu.nodes['Fault_3496']['weight']=new_weight
Gloopu.nodes['Fault_12647']['weight']=new_weight
Gloopu.nodes['Fault_2235']['weight']=new_weight
#Gloopu.nodes['Fault_6809']['weight']=new_weight
#Gloopu.nodes['Fault_7516']['weight']=new_weight
#Gloopu.nodes['Fault_15421']['weight']=new_weight
#print(Gloopu.nodes['Fault_3498'])
def func(u, v, d):
    node_u_wt = Gloopu.nodes[u].get("weight", 1)
    node_v_wt = Gloopu.nodes[v].get("weight", 1)
    edge_wt = d.get("weight", 1)
    return node_u_wt / 2 + node_v_wt / 2 + edge_wt

distances={}
for anode in Gloop.nodes:
    if(source != anode):
        path = nx.dijkstra_path(Gloopu, source=source, target=anode,weight=func)
        edist=nx.resistance_distance(Gloopu, nodeA=source, nodeB=anode,weight='weight')
        ddist=nx.dijkstra_path_length(Gloopu, source=source, target=anode, weight=func)
        distances[anode]={'source':source,'dest':anode,'edist':edist,'ddist':ddist,'path':str(list(path))}

geology_exploded['uid']=geology_exploded.index.astype("string")
distances_node=pd.DataFrame.from_dict(distances,orient='index')
distances_node['uid']=distances_node['dest']
geology_exploded_dist=geology_exploded.merge(distances_node, on='uid')

euc_dist={}
source_pt=Point((geology_exploded.loc[int(source)].geometry.centroid.x,geology_exploded.loc[int(source)].geometry.centroid.y))
for ind,g in geology_exploded.iterrows():
    if(str(ind) != source):
        dest_pt=g.geometry.centroid
    dist=source_pt.distance(dest_pt)
    euc_dist[ind]={'source':source,'dest':str(ind),'euc_dist':dist}

distances_euc=pd.DataFrame.from_dict(euc_dist,orient='index')
distances_euc['uid']=distances_euc['dest']
geology_exploded_dist=geology_exploded_dist.merge(distances_euc, on='uid')
geology_exploded_dist.to_file(os.path.join(gis_path, 'geol_dist.shp'))

### can alter specific fault weights by fault length/strat offset/length....
### can alter specific strat weights by lithology/area/volume


In [13]:
paths = nx.all_pairs_dijkstra_path(Gloopu,weight=func)

In [14]:
paths

<generator object all_pairs_dijkstra_path at 0x000001954E1F3EC8>

In [22]:
dict(paths)

{'0': {'0': ['0'],
  '54': ['0', '54'],
  '4': ['0', '4'],
  'Fault_2235': ['0', 'Fault_2235'],
  'Fault_2843': ['0', 'Fault_2843'],
  'Fault_5471': ['0', 'Fault_2235', 'Fault_5471'],
  '30': ['0', 'Fault_2235', '30'],
  '31': ['0', 'Fault_2235', '31'],
  '33': ['0', 'Fault_2235', '33'],
  '42': ['0', 'Fault_2235', '42'],
  '43': ['0', 'Fault_2235', '43'],
  '50': ['0', 'Fault_2235', '50'],
  '51': ['0', 'Fault_2235', '51'],
  '55': ['0', 'Fault_2235', '55'],
  '85': ['0', 'Fault_2235', '85'],
  '86': ['0', 'Fault_2235', '86'],
  '89': ['0', 'Fault_2235', '89'],
  '90': ['0', 'Fault_2235', '90'],
  'Fault_5252': ['0', 'Fault_2235', 'Fault_5252'],
  'Fault_962': ['0', 'Fault_2843', 'Fault_962'],
  '1': ['0', 'Fault_2843', '1'],
  '16': ['0', 'Fault_2843', '16'],
  '77': ['0', 'Fault_2843', '77'],
  '78': ['0', 'Fault_2843', '78'],
  '104': ['0', 'Fault_2843', '104'],
  '108': ['0', 'Fault_2843', '108'],
  '109': ['0', 'Fault_2843', '109'],
  '15': ['0', 'Fault_2235', '30', '15'],
  'Fau

In [41]:
dist=np.zeros((len(Gloopu.nodes()),len(Gloopu.nodes())))
nodes=Gloopu.nodes()
nodeA='102'
a=0
b=0
for nodeA in nodes:
    for nodeB in nodes:
        if(nodeA!=nodeB):
            dist[a,b]=nx.resistance_distance(Gloopu, nodeA=nodeA, nodeB=nodeB,weight='weight')
        b=b+1
    a=a+1
    b=0

In [1]:
for a in range(len(nodes)):
    dist[a,a]=0
    
%matplotlib inline
from matplotlib import pyplot as plt
plt.imshow(dist,interpolation='nearest',cmap='rainbow')
plt.show()

NameError: name 'nodes' is not defined

In [71]:
dist.max(),dist.min(),dist.mean()

(57.248457641207345, 0.0, 7.465418849041403)

In [72]:
index=np.argmax(dist)

row=int(index/len(nodes))
col=index-(row*len(nodes))
index,row,col

(8679, 47, 125)